In [1]:
import pandas as pd
from collections import OrderedDict
import json, os, time, datetime

# Making unique stop names list

with routes and even depots comma-separated


In [2]:
dataCleanedCSV = 'data cleaning/stopnames-datacleaning-17.12.18.csv'

In [3]:
df = pd.read_csv(dataCleanedCSV, dtype=str)
df.head()

sr                              folder   jsonFile routeName direction_id  \
0  0  routejsons2/26.11.18/BKP - Santosh  113M.json      113M            0   
1  1  routejsons2/26.11.18/BKP - Santosh  113M.json      113M            0   
2  2  routejsons2/26.11.18/BKP - Santosh  113M.json      113M            0   
3  3  routejsons2/26.11.18/BKP - Santosh  113M.json      113M            0   
4  4  routejsons2/26.11.18/BKP - Santosh  113M.json      113M            0   

  stop_sequence     ORIGINAL stop_name_dataclean  
0             1  Mehdipatnam         Mehdipatnam  
1             2  SD Hospital         SD Hospital  
2             3         NMDC                NMDC  
3             4   Masab Tank          Masab Tank  
4             5      P House             P House

In [4]:
def extractDepot(root):
    folderDepotHolder = root.split('/')
    if len(folderDepotHolder) > 2:
        folderDepot = folderDepotHolder[2].split()[0]
        return folderDepot
    else:
        print('\n\nAlert! No depot found for',root)
        return ''

In [5]:
df['depot'] = df['folder'].apply(extractDepot)

In [6]:
df.sample(10)

sr                              folder           jsonFile  \
19641  19656   routejsons2/28.11.18/JDM - Vishal          29CD.json   
67551  68170     routejsons2/6.12.18/UPL - Surya           493.json   
55180  55762  routejsons2/6.12.18/HN1 - akkshath           462.json   
20614  20633   routejsons2/28.11.18/JDM - Vishal  83J_272G_JDM.json   
18172  18179   routejsons2/28.11.18/JDM - Vishal      19KJ_JDM.json   
68527  69152      routejsons2/8.12.18/FMA - self          254K.json   
59472  60089    routejsons2/6.12.18/IBP - Girish         277D_.json   
40048  40245   routejsons2/5.12.18/MHRM - Vishal      527_MHRM.json   
57018  57619   routejsons2/6.12.18/HN2 - Dhanush            1V.json   
28446  28543     routejsons2/4.12.18/HPT - Surya         211BA.json   

          routeName direction_id stop_sequence          ORIGINAL  \
19641          29CD            0            21         NTR Nagar   
67551           493            0            16       Uppal Depot   
55180           462            1             9   Abdhullapur Met   
20614  83J/272G_JDM            1            16     Bharath Nagar   
18172      19KJ_JDM            0            17     Care Hospital   
68527          254K            1            21      Engine Bowli   
59472         277D*            1             5  Sri Indu College   
40048      527_MHRM            0             7      Farukh Nagar   
57018            1V            0             9       Narayanguda   
28446         211BA            0            14        Water Tank   

      stop_name_dataclean depot  
19641           NTR Nagar   JDM  
67551         Uppal Depot   UPL  
55180       Abdullapurmet   HN1  
20614       Bharath Nagar   JDM  
18172       Care Hospital   JDM  
68527        Engine Bowli   FMA  
59472    Sri Indu College   IBP  
40048         Farooqnagar  MHRM  
57018         Narayanguda   HN2  
28446          Water Tank   HPT

In [7]:
# using the custom function approach to do all the grouping and processing at a go.
def listORone(ser):
    return (', '.join(set(ser)),len(set(ser))) if len(set(ser))>1 else (ser.iloc[0],1)
    

def names_grouping(x):
    routes, num_routes = listORone(x['routeName'])
    depots, num_depots = listORone(x['depot'])
    rest = OrderedDict({
        'count': len(x),
        'routes': routes,
        'num_routes': num_routes,
        'depots': depots,
        'num_depots': num_depots
    })
    return pd.Series(rest)        

In [8]:
stopsDF = df.groupby('stop_name_dataclean').apply(names_grouping).reset_index()
stopsDF.sample(10)

stop_name_dataclean  count  \
2550                Omkar Nagar X Road      2   
2145                      Masjid Banda     44   
2173  Mehdipatnam Depot / Amba Theatre      4   
1310                       IDPL Colony    163   
1507                    Jumerath Bazar      4   
2479                    New Nallakunta      4   
2016                           Mahavir     84   
922                          Erravelli      2   
2854                          RS Tanda      8   
1491               Jubilee Bus Station    253   

                                                 routes  num_routes  \
2550                                                279           1   
2145  156L/216DLF, 216MG, 104A/216, 217D/L, 316, 195...          19   
2173                                   49M/T/250, 49M/T           2   
1310  9K_JDM, 171R_JDM, 9X/230X_JDM, 9X2752K, 9X272G...          81   
1507                                          72JL, 80S           2   
2479                                      107VR, 107V/R           2   
2016  65, 216MG, 156L, 6NG, 5K/16C, 222, 216T, 113M/...          36   
922                                                 212           1   
2854                                 580, 577, 579, 578           4   
1491  44EX, 10H/25I, 291, 23GF, 212/567M, 49E/22D, 2...         117   

                                                 depots  num_depots  
2550                                                CNT           1  
2145                    MSRD2, BKP, HCU, MDN, KCG, DSNR           6  
2173                                                MPM           1  
1310  BKP, RN1, FQNR, JDM, KPL, MPM, HN2, FMA, RJNR,...          12  
1507                                          RJNR, HN2           2  
2479                                           HN1, BGD           2  
2016  MSRD2, BKP, CCL, HCU, MPM, HN2, MDN, KGD, KCG,...          12  
922                                                 RN1           1  
2854                                                KGD           1  
1491  RN1, FQNR, KPL, JDM, HCU, HN2, IBP, MI2, KCG, ...          17

In [9]:
# sort dataframe while ignoring case. From https://stackoverflow.com/a/41656788/4355695
stopsDF2 = stopsDF.iloc[stopsDF.stop_name_dataclean.str.lower().argsort()].reset_index(drop=True)

In [10]:
stopsDF2.to_csv('analysis/unique_stop_names.csv',index_label='sr')

In [11]:
len(stopsDF2)

3891

### manually format the csv to a .xlsx for sharing